<a href="https://colab.research.google.com/github/oscaryas/MAT1510/blob/main/Not_All_Language_Model_Features_Are_One_Dimensionally_Linear_.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# TASK

Your task is to visualize the token embeddings corresponding to the days of the week to see if any structure emerges in their representations.

## Part 1: Load the Model

Use the `transformers` library to load the `GPT-2` model and its tokenizer. The model can be found at: https://huggingface.co/openai-community/gpt2.

## Part 2: Implement `get_day_embeddings()`.
The function `get_day_embeddings` takes `layer_idx` as input and returns a dictionary mapping each weekday to a list of token representations. Each list contains the representations of tokens corresponding to that weekday, extracted from the output of the specified decoder layer.

### Part A: Prompt the Model

Pass through the model each prompt provided in `days_contexts` where `{day}` is replaced with each of the 7 days of the week (see `days`). In other words, you should be prompting the model with `7*len(days_contexts)` many prompts.

### Part B. Extract the Hidden States

Update Part A. such that the hidden states (i.e. the ouputs of each decoder layer) are saved. Define a variable, `hidden_states` that stores the hidden states corresponding to `layer_idx`.

### Part C. Extract Representations of Day Tokens
From `hidden_states`, extract **specifically** the tokens that corresponds to the `day` and append it to the list in `day_embeddings[day]`. Note that each `day` is repreented by a single token in GPT-2's tokenizer. Thus, this should be a *vector* whose dimension corresponds to the hidden dimension of the model.

## Part 3: Perform PCA on the Means

### Part A. Calculate the means and normalize
For each `day`, calculate the mean of their hidden states. Take the mean vector and normalize it so it's unit norm. Store the normalized mean vectors into a numpy array called `mean_days_array`. (This array should have dimension 7x`hidden_dim`),


### Part B. Run PCA and Plot
Run the final block of code. This code is functioning and should not be changed. Provide a 1-2 sentence description of what you see.



In [ ]:
from transformers import GPT2Tokenizer, GPT2Model
import torch
import numpy as np
import imageio
from sklearn.decomposition import PCA
import matplotlib.pyplot as plt
from matplotlib.lines import Line2D
import plotly.graph_objects as go

In [ ]:

# IMPLEMENT PART 1
tokenizer = GPT2Tokenizer.from_pretrained("gpt2")
model = GPT2Model.from_pretrained('gpt2')

/usr/local/lib/python3.12/dist-packages/huggingface_hub/utils/_auth.py:104: UserWarning: 
Error while fetching `HF_TOKEN` secret value from your vault: 'Requesting secret HF_TOKEN timed out. Secrets can only be fetched when running from the Colab UI.'.
You are not authenticated with the Hugging Face Hub in this notebook.
If the error persists, please let us know by opening an issue on GitHub (https://github.com/huggingface/huggingface_hub/issues/new).
  warnings.warn(


tokenizer_config.json:   0%|          | 0.00/26.0 [00:00<?, ?B/s]

vocab.json:   0%|          | 0.00/1.04M [00:00<?, ?B/s]

merges.txt:   0%|          | 0.00/456k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/1.36M [00:00<?, ?B/s]

config.json:   0%|          | 0.00/665 [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/548M [00:00<?, ?B/s]

In [ ]:
days_contexts = [
    "Last {day} I went to the store.",
    "Every {day} morning I wake up early.",
    "Next {day} we have a meeting.",
    "On {day} afternoon,",
    "This {day} will be busy.",
    "{day} is my favorite day.",
    "I love {day}s!",
    "Remember {day} night?",
    "See you {day}!",
    "Happy {day}!",
    "Since {day}, things changed.",
    "By {day} everything was ready.",
    "Until {day} we waited.",
    "From {day} onward,",
    "The {day} meeting was productive.",
    "{day} evening we went out.",
    "Can we meet {day}?",
    "I work on {day}.",
    "{day} is always hectic.",
    "Looking forward to {day}.",
    "Last {day} was amazing.",
    "Every {day} I exercise.",
    "Next {day} is important.",
    "{day} morning coffee is the best.",
    "I hate {day}s.",
    "{day} night plans?",
    "See you next {day}.",
    "This {day} off work.",
    "{day} deadline approaching.",
    "Planning for {day}.",
    "{day} is usually quiet.",
    "I always rest on {day}.",
    "{day} classes are canceled.",
    "Let's meet on {day}.",
    "{day} afternoon tea.",
    "Every {day} I cook.",
    "{day} is gym day.",
    "I love {day} mornings.",
    "{day} feels long.",
    "This {day} is special.",
    "On {day} we dine out.",
    "{day} traffic is terrible.",
    "I work from home on {day}.",
    "{day} lunch meeting.",
    "Looking forward to {day} night.",
    "{day} is laundry day.",
    "Every {day} I read.",
    "{day} morning run.",
    "This {day} was exhausting.",
    "Next {day} is free.",
    "{day} grocery shopping.",
    "I sleep in on {day}.",
    "{day} is my rest day.",
    "Planning {day} activities.",
    "{day} evening relaxation.",
    "This {day} went by fast.",
    "{day} is always productive.",
    "Last {day} was stressful.",
    "Every {day} feels different.",
    "{day} is date night.",
    "I clean on {day}.",
    "{day} brunch plans.",
    "Next {day} looks busy.",
    "{day} is my favorite.",
    "This {day} has been great.",
    "{day} afternoon nap.",
    "Every {day} I meal prep.",
    "{day} morning yoga.",
    "Last {day} I traveled.",
    "{day} is family time.",
    "I volunteer on {day}.",
    "{day} is for errands.",
    "This {day} I'm staying in.",
    "{day} market visit.",
    "Every {day} routine.",
    "{day} is movie night.",
    "Next {day} appointment.",
    "{day} evening walk.",
    "This {day} was peaceful.",
    "{day} is hectic usually.",
    "Last {day} weather was nice.",
    "Every {day} I journal.",
    "{day} is for hobbies.",
    "I study on {day}.",
    "{day} afternoon meetings.",
    "This {day} is different.",
    "{day} morning commute.",
    "Every {day} has its charm.",
    "{day} evening plans.",
    "Next {day} is vacation.",
    "{day} is my busy day.",
    "This {day} I'll relax.",
    "{day} morning meditation.",
    "Every {day} brings new things.",
    "{day} is always interesting.",
    "Last {day} concert.",
    "{day} is soccer practice.",
    "This {day} party tonight.",
    "{day} morning sunshine.",
    "Every {day} I'm grateful for.",
]

days = ["Monday", "Tuesday", "Wednesday", "Thursday", "Friday", "Saturday", "Sunday"]

def get_day_embeddings(model, tokenizer, days, contexts, layer_idx):
    """Extract embeddings for the day token in each sentence"""
    import torch

    day_embeddings = {day: [] for day in days}

    day_token_ids = {
        day: tokenizer.encode(day, add_special_tokens=False)[0]
        for day in days
    }
    print(day_token_ids)

    model.eval()
    with torch.no_grad():
        for day in days:
            day_token_id = day_token_ids[day]

            for context in contexts:
                text = context.format(day = day)
                inputs = tokenizer(text, return_tensors="pt")
                input_ids = inputs["input_ids"]
                # print(text)

                outputs = model(**inputs, output_hidden_states=True)
                all_hidden_states = outputs.hidden_states

                hidden_states = all_hidden_states[layer_idx + 1]
                print(hidden_states)

                positions = (input_ids[0] == day_token_id).nonzero(as_tuple=False).flatten()

                for pos in positions:
                    token_vec = hidden_states[0, pos, :].clone()
                    day_embeddings[day].append(token_vec)

    return day_embeddings


In [ ]:
layer_idx = 10
day_embeddings = get_day_embeddings(model, tokenizer, days, days_contexts, layer_idx)

{'Monday': 23810, 'Tuesday': 26133, 'Wednesday': 27150, 'Thursday': 25381, 'Friday': 20610, 'Saturday': 19844, 'Sunday': 21934}
tensor([[[  2.7975,  -1.7203,   0.9274,  ...,  -2.2488,  -0.2468,  -1.1293],
         [  1.5155,  -5.7559,   3.0275,  ...,   0.9094,  -2.5711, -12.3325],
         [  0.7430,  -5.9089,   3.7784,  ...,  -0.0883,   1.3928,  -1.3030],
         ...,
         [  1.9007,  -4.2995,   3.1567,  ...,  -0.0165,   0.6899,   2.6795],
         [  1.5591,  -2.0944,  -9.4896,  ...,  -1.5902,  -2.0466,  -2.4014],
         [  0.7846,  -7.8177,  -4.2424,  ...,   1.2164,  -4.1207,  -2.6574]]])
tensor([[[  0.9710,  -0.2503,   0.5082,  ...,  -1.1300,  -0.4822,  -0.7201],
         [  0.9837,  -3.4157,  -0.0270,  ...,   3.2265,  -6.3999, -12.4034],
         [  3.8288,  -2.9130,   1.1506,  ...,   5.5406,  -4.9703, -13.8925],
         ...,
         [  4.8256,   1.8416,  -5.4596,  ...,  12.8910,   6.9336,   1.2802],
         [  7.3402,  -6.5049, -13.4704,  ...,   9.0711,   4.7160,   1.57

In [ ]:
day_embeddings

{'Monday': [tensor([ 1.3715e+00, -1.8125e+00,  7.2794e-01, -5.4846e-01,  3.1565e-01,
          -1.7322e+00,  1.5101e+00, -2.5126e+00, -3.1386e+00, -6.3686e-02,
           8.4010e-01,  7.0928e-01, -1.5754e+00, -8.7930e-01, -1.1397e+00,
           8.5877e-01, -1.6247e+00, -7.1935e-01,  1.5044e+00, -8.8021e-01,
           2.5687e+00, -5.8722e-01, -5.4554e-01,  3.6304e-01,  1.6653e-01,
           1.0702e+00,  5.8930e-01, -4.7219e-01, -4.4117e-01, -1.7728e+00,
           1.5464e+00, -1.1275e-02,  9.0371e-01, -1.2489e-01, -1.0323e+00,
           1.6758e+00,  3.9484e+00, -9.8086e-01, -8.7431e-01,  1.0470e+00,
          -1.1307e+00,  1.7675e+00,  1.4657e+00, -1.6914e+00,  9.3027e-01,
           8.6354e-01,  9.7089e-01, -7.5309e-01, -2.3714e+00, -3.8242e-01,
          -1.2573e-03,  1.2234e+00,  1.7662e+00,  2.5721e-01, -4.8034e-01,
           3.5459e+00,  2.0997e+00, -3.4982e+00, -1.0130e+00, -1.0974e+00,
          -1.9560e-01,  7.5989e-02, -1.0900e-01,  7.8855e-01,  2.7852e+00,
          -1.06

In [ ]:
all_vectors = []
all_labels = []

for day in days:
    for vec in day_embeddings[day]:
        all_vectors.append(vec)
        all_labels.append(day)

all_vectors = torch.stack(all_vectors)


pca = PCA(n_components=2)
points_pca = pca.fit_transform(all_vectors)

In [ ]:
print(points_pca)

[[-7.43147965 -0.80820512]
 [-7.43147965 -0.80820512]
 [-7.43147965 -0.80820512]
 [-7.43147965 -0.80820512]
 [-7.43147965 -0.80820512]
 [-7.43147965 -0.80820512]
 [-7.43147965 -0.80820512]
 [-7.43147965 -0.80820512]
 [-7.43147965 -0.80820512]
 [-7.43147965 -0.80820512]
 [-7.43147965 -0.80820512]
 [-7.43147965 -0.80820512]
 [-7.43147965 -0.80820512]
 [-7.43147965 -0.80820512]
 [-7.43147965 -0.80820512]
 [-7.43147965 -0.80820512]
 [-7.43147965 -0.80820512]
 [-7.43147965 -0.80820512]
 [-7.43147965 -0.80820512]
 [-7.43147965 -0.80820512]
 [-7.43147965 -0.80820512]
 [-7.43147965 -0.80820512]
 [-7.43147965 -0.80820512]
 [-7.43147965 -0.80820512]
 [-7.43147965 -0.80820512]
 [-7.43147965 -0.80820512]
 [-7.43147965 -0.80820512]
 [-7.43147965 -0.80820512]
 [-7.43147965 -0.80820512]
 [-7.43147965 -0.80820512]
 [-7.43147965 -0.80820512]
 [-7.43147965 -0.80820512]
 [-7.43147965 -0.80820512]
 [-7.43147965 -0.80820512]
 [-7.43147965 -0.80820512]
 [-7.43147965 -0.80820512]
 [-7.43147965 -0.80820512]
 

In [ ]:
# RUN PART 3 PART B HERE
color_map = {
    "Monday":    '#1f77b4',
    "Tuesday":   '#ff7f0e',
    "Wednesday": '#2ca02c',
    "Thursday":  '#d62728',
    "Friday":    '#9467bd',
    "Saturday":  '#8c564b',
    "Sunday":    '#e377c2'
}

point_colors = [color_map[d] for d in all_labels]


day_colors = ['#1f77b4', '#ff7f0e', '#2ca02c', '#d62728', '#9467bd', '#8c564b', '#e377c2']
fig = go.Figure(data=[go.Scatter(
    x=points_pca[:, 0],
    y=points_pca[:, 1],
    mode='markers',
    marker=dict(
        size=7,
        color=point_colors,
        opacity=0.85
    ),
    text=all_labels,
    hovertemplate='<b>%{text}</b><br>' +
                  'PC1: %{x:.4f}<br>' +
                  'PC2: %{y:.4f}<br>' +
                  '<extra></extra>'
)])

fig.update_layout(
    title=dict(
        text=f'All Day Embeddings - GPT-2 Layer {layer_idx}',
        font=dict(size=22)
    ),
    xaxis_title='PCA Component 1',
    yaxis_title='PCA Component 2',
    plot_bgcolor='rgb(240, 240, 240)',
    xaxis=dict(gridcolor='white'),
    yaxis=dict(gridcolor='white'),
    width=950,
    height=720
)

fig.show()